## ライブラリのインポート

In [12]:
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

## 学習用のCNNを準備

In [35]:
def cnn_model_fn(features, labels, mode):
    """Model Function for CNN"""
    # Input Layer --------------------------------------------------
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
    # tf の layers では入力tensorは[batch_size, image_width, image_height, channels]である必要がある
    # batch_size は -1 にしておくことにより動的に決定できる
    
    # Convolutional Layer #1 : フィルタにより畳み込み演算を行う ----------
    conv1 = tf.layers.conv2d(
                             inputs=input_layer,
                             filters=32, 
                             kernel_size=[5, 5], # [width, height] もし平方なら kernel_size=5 と書ける
                             padding="same", # valid or same(デフォルトはvalid) sameにすると入力と出力でサイズが保存される
                             activation=tf.nn.relu
                            )
    # 上の場合、出力は[batch_size, 28, 28, 32]になる
    
    # Pooling Layer #1 : データの次元数を減らし速度上昇を狙う -------------
    pool1 = tf.layers.max_pooling2d(
                                    inputs=conv1,
                                    pool_size=[2, 2], # 平方なら略せる
                                    strides=2 # フィルタの移動量　タプルやリストを渡すことでw:hの移動比を変えられる
                                   )
    # max_pooling2dでは範囲内から最大のもののみ残すことで次元を削減する
    # 上の場合、出力は[batch_size, 14, 14, 32]になる
    
    # Convolutional Layer #2 ----------------------------------------
    conv2 = tf.layers.conv2d(
                             inputs=pool1,
                             filters=64,
                             kernel_size=[5, 5],
                             padding="same",
                             activation=tf.nn.relu
                            )
    # 出力は[batch_size, 14, 14, 64]
    
    # Pooling Layer #2 -----------------------------------------------
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)
    # 出力は[batch_size, 7, 7, 64]
    
    # Dense Layer(Fully Connected Layer) -----------------------------
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64]) # 特徴マップを2次元[batch_size, features]に形成
    # 出力は[batch_size, 3136]
    dense = tf.layers.dense(
                            inputs=pool2_flat,
                            units=1024, # dense layer の neuron数(ノードの数)
                            activation=tf.nn.relu
                           )
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=(mode == tf.estimator.ModeKeys.TRAIN))
    # dropout は過学習を防ぐために学習中にいくつかのノードをないものとして扱うこと
    # rate=0.4 は、40%の確率でランダムにノードがドロップアウトすることを示す
    # mode==TRAIN のときのみ
    # 出力は[batch_size, 1024]
    
    # Logits Layer : 0-9 の結果を出力するための層 ------------------------
    logits = tf. layers.dense(inputs=dropout, units=10)
    # 出力は[batch_size ,10]
    
    # Generate Predictions -------------------------------------------
    predictions = {
        "classes": tf.argmax(input=logits, axis=1), # axis=1(10このうち)から最大のものを取り出す
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    # 予測としてクラス分類結果を取り出したりそれぞれの分類確率を見たりできるようにする
    # name をつけておくことで後から参照できる
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    
    # Calculate Loss : 訓練、評価のためにロス関数を計算する -----------------
    onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
    # 1, 3, 4,...のように表される正解ラベルを "one-hot encoding"する
    # 1 -> [0, 1, 0, 0, 0, 0, 0, 0, 0] のようにすること
    # ラベルをintにキャストして渡し、分類数を10と指定している
    loss = tf.losses.softmax_cross_entropy(
        onehot_labels=onehot_labels, logits=logits)
    # 多値分類ではクロスエントロピーがロスとしてよく用いられる
    
    # Configure the Training Optimizer : ロスを最適化する ----------------
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
    # よくわからん: https://www.tensorflow.org/get_started/custom_estimators#defining-the-training-op-for-the-model
    
    # Add evaluation metrics -------------------------------------------
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])
    }
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)
    # これもよくわからんね

## データセット読み込み

In [36]:
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
# train -> 55,000 datas
eval_data = mnist.test.images
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
# eval -> 10,000 datas

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [37]:
# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x1c365caf28>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


## ログ取得

In [38]:
tensors_to_log = {"probabilities": "softmax_tensor"} # keyがログのラベルになる　中身はtensorのname
logging_hook = tf.train.LoggingTensorHook(
    tensors=tensors_to_log, every_n_iter=50) # 50steps ごとに記録される

## 学習(training)

In [39]:
# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100, # ミニバッチのサイズ
    num_epochs=None, # steps に達するまで行う
    shuffle=True) # データをシャッフルして渡す
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[0.10746317 0.09032356 0.09012149 0.09576146 0.10909957 0.10876828
  0.09606209 0.10082278 0.10597187 0.09560578]
 [0.09077585 0.09399507 0.09418496 0.0992732  0.10549477 0.10249828
  0.10377657 0.10877391 0.09921291 0.10201449]
 [0.09278427 0.10174573 0.09298731 0.09207396 0.10084625 0.10879135
  0.10395775 0.10668024 0.09144597 0.10868712]
 [0.09628892 0.10491346 0.08827397 0.09612924 0.10804842 0.10914665
  0.10619318 0.09651469 0.09198609 0.10250542]
 [0.08994366 0.10833791 0.09481905 0.09851975 0.10818147 0.1031687
  0.11038195 0.08953767 0.09172581 0.10538401]
 [0.09870773 0.10027622 0.0937014  0.09565884 0.11876549 0.09755366
  0.09

INFO:tensorflow:loss = 2.311376, step = 1
INFO:tensorflow:probabilities = [[0.09452298 0.09768067 0.09767743 0.09409789 0.1034515  0.09441514
  0.10373586 0.10737018 0.11106861 0.09597974]
 [0.10179819 0.09234414 0.10046636 0.09646497 0.10687175 0.09647585
  0.09857737 0.10809483 0.11034254 0.08856399]
 [0.09411339 0.0974528  0.091685   0.09538414 0.09657455 0.10913046
  0.09738047 0.10723097 0.11789827 0.09315   ]
 [0.10017535 0.09319389 0.09691074 0.0968464  0.10350873 0.09581967
  0.10696183 0.1095894  0.10396127 0.09303278]
 [0.09086812 0.10035802 0.09357246 0.08785026 0.10556483 0.11230209
  0.09383299 0.10733115 0.10839115 0.09992893]
 [0.09009148 0.1075378  0.09474278 0.09259873 0.1038333  0.09135123
  0.11293214 0.09454689 0.10298514 0.10938045]
 [0.10814275 0.09900467 0.09808623 0.10465223 0.08813143 0.10272433
  0.09573637 0.1053979  0.09467457 0.10344953]
 [0.10524178 0.09750172 0.08983867 0.09377442 0.10661015 0.09878533
  0.09879854 0.11375728 0.10287173 0.09282044]
 [0.09

INFO:tensorflow:global_step/sec: 5.70317
INFO:tensorflow:probabilities = [[0.09353797 0.10503604 0.09413461 0.08693765 0.10127355 0.11449174
  0.11090836 0.09357809 0.09855317 0.10154881]
 [0.11003485 0.09425085 0.09321327 0.08060597 0.09887438 0.10823485
  0.10157625 0.1084925  0.09631178 0.10840538]
 [0.09658983 0.09925116 0.09713373 0.09245834 0.10392331 0.10115986
  0.09777915 0.10550278 0.10619144 0.10001038]
 [0.1030978  0.10591578 0.09167036 0.10271759 0.10607664 0.09486807
  0.10036393 0.09931505 0.09676912 0.09920573]
 [0.10342376 0.09185566 0.09522012 0.09275693 0.11397057 0.09667346
  0.0937187  0.10812382 0.1037131  0.10054388]
 [0.08902505 0.09482263 0.09316227 0.08217736 0.10821058 0.0997765
  0.11791098 0.10629514 0.11032164 0.09829792]
 [0.08553104 0.1111242  0.10222738 0.09425521 0.10800229 0.09270941
  0.10389025 0.11079364 0.09648286 0.09498377]
 [0.09634902 0.10362401 0.09271448 0.10086074 0.09444541 0.11256813
  0.10959931 0.09616981 0.09436832 0.09930079]
 [0.0940

INFO:tensorflow:loss = 2.28989, step = 101 (17.534 sec)
INFO:tensorflow:probabilities = [[0.08805953 0.10376167 0.08513162 0.08443899 0.08579275 0.11588357
  0.11311253 0.10771458 0.10518037 0.11092439]
 [0.09989561 0.09936594 0.09665278 0.1027472  0.10697781 0.09562107
  0.0985625  0.10384085 0.0958648  0.10047147]
 [0.09928499 0.10014411 0.09989718 0.09368021 0.09920156 0.09524215
  0.0975721  0.10694341 0.10803077 0.10000352]
 [0.10111796 0.09235727 0.10289691 0.08704653 0.09337309 0.10243404
  0.10082985 0.10576498 0.11379462 0.10038481]
 [0.09569449 0.10849146 0.09740219 0.0811782  0.09666294 0.10477062
  0.10482741 0.10520519 0.10463289 0.10113464]
 [0.09809393 0.09518509 0.09835907 0.09286834 0.11247323 0.09055477
  0.10136323 0.10724713 0.10719396 0.09666121]
 [0.09979789 0.09223688 0.08929259 0.10332457 0.11083742 0.10114143
  0.10262402 0.09828845 0.10736366 0.09509303]
 [0.09791885 0.10379916 0.09921399 0.09520917 0.09126527 0.09853238
  0.10061705 0.10381959 0.11177611 0.09

INFO:tensorflow:global_step/sec: 5.38509
INFO:tensorflow:probabilities = [[0.10154894 0.09810597 0.09427708 0.10256092 0.0960814  0.09486037
  0.10144775 0.11202796 0.10848774 0.09060178]
 [0.10122814 0.09873381 0.09867901 0.10299537 0.09819006 0.10586074
  0.09129224 0.10361645 0.10099604 0.09840816]
 [0.10086    0.10081892 0.10073881 0.10209785 0.09607858 0.10016391
  0.09863329 0.09714098 0.10396126 0.0995065 ]
 [0.0960965  0.10835989 0.0896486  0.08861944 0.09621416 0.10212073
  0.10542081 0.10683692 0.10223731 0.10444567]
 [0.09499001 0.10462879 0.09189849 0.10147368 0.09699059 0.10774148
  0.10036888 0.08801291 0.10611523 0.10777996]
 [0.10312252 0.09674083 0.07767757 0.10124616 0.11185946 0.09735053
  0.09939995 0.10262613 0.10821225 0.10176466]
 [0.10091618 0.09864628 0.09139588 0.1006008  0.10387722 0.0921133
  0.10973556 0.09411144 0.10951238 0.09909098]
 [0.10475332 0.0905756  0.11745682 0.09913366 0.0930364  0.10317493
  0.10657987 0.10103632 0.09777321 0.08647981]
 [0.1119

...

INFO:tensorflow:global_step/sec: 6.1118
INFO:tensorflow:probabilities = [[0.00000285 0.998004   0.00009986 0.00030384 0.00051762 0.00010056
  0.00012918 0.00007107 0.00073665 0.00003441]
 [0.00018628 0.00000045 0.00000069 0.00013797 0.00001731 0.99944764
  0.00000648 0.00002133 0.00017775 0.00000409]
 [0.00014455 0.00000174 0.99474937 0.00023732 0.0000015  0.00008487
  0.00003388 0.00424947 0.00044648 0.00005079]
 [0.00000095 0.00777064 0.03121728 0.888493   0.01876232 0.00033219
  0.00015248 0.01380202 0.01233877 0.02713034]
 [0.00000107 0.00002685 0.00000659 0.00022511 0.00002051 0.00007509
  0.00000008 0.9988808  0.00000587 0.00075812]
 [0.00000015 0.000003   0.9993148  0.00067146 0.         0.
  0.00000009 0.         0.00001053 0.        ]
 [0.00000002 0.00000023 0.00002765 0.00073314 0.00000022 0.00000046
  0.         0.99918383 0.00000091 0.00005352]
 [0.0000189  0.9925345  0.00005439 0.00018548 0.00438525 0.00001393
  0.00005094 0.00113064 0.00132537 0.0003006 ]
 [0.9957883  0.0

INFO:tensorflow:loss = 0.22012912, step = 19801 (16.363 sec)
INFO:tensorflow:probabilities = [[0.00002847 0.9982668  0.00041529 0.00002903 0.00016754 0.00000173
  0.00036211 0.00017247 0.00055582 0.00000061]
 [0.00000079 0.00000094 0.00338984 0.01748839 0.00035774 0.00005317
  0.00000005 0.9086467  0.0003116  0.06975082]
 [0.0000112  0.00000206 0.00014668 0.00000257 0.00020798 0.00002394
  0.9994998  0.00000001 0.00010514 0.00000052]
 [0.00005152 0.9943522  0.00060982 0.00023083 0.00004409 0.00002188
  0.000035   0.00428049 0.00027923 0.00009488]
 [0.00034233 0.0000871  0.9831654  0.00453571 0.00023444 0.00039937
  0.00005518 0.00330358 0.00011485 0.00776214]
 [0.00000895 0.00006524 0.00004884 0.00004763 0.00088173 0.00059482
  0.99830544 0.00000004 0.00004624 0.00000113]
 [0.00000007 0.00000008 0.00000119 0.00000134 0.98806214 0.00000606
  0.00000036 0.00017565 0.00045319 0.01129985]
 [0.00004162 0.00001061 0.0016607  0.00000066 0.00166399 0.00014476
  0.99638295 0.         0.00009272

INFO:tensorflow:global_step/sec: 5.97239
INFO:tensorflow:probabilities = [[0.00000146 0.00000143 0.00002823 0.00001604 0.9742154  0.0000086
  0.00002897 0.00059924 0.00022698 0.02487365]
 [0.00000018 0.         0.9998604  0.00011813 0.00000001 0.00000008
  0.00000002 0.00000997 0.00001118 0.00000007]
 [0.00000343 0.00000053 0.00027397 0.00060181 0.00000127 0.00006155
  0.00000149 0.00000223 0.99868995 0.00036385]
 [0.00000001 0.         0.00000015 0.00000126 0.00000001 0.00000361
  0.         0.99997544 0.00000008 0.00001948]
 [0.00004019 0.97623    0.00092155 0.00349237 0.00000256 0.00193582
  0.00101017 0.00000123 0.01636064 0.00000548]
 [0.00669783 0.00067797 0.0005625  0.00048133 0.00073684 0.59583867
  0.38718143 0.00000638 0.00759415 0.00022286]
 [0.00037299 0.00045286 0.00017149 0.00218504 0.00025572 0.00131871
  0.00000141 0.9630621  0.00033722 0.03184255]
 [0.00000381 0.00000086 0.00009501 0.00000488 0.9989102  0.00000208
  0.00012493 0.00000382 0.00000609 0.00084827]
 [0.0000

INFO:tensorflow:loss = 0.07342072, step = 19901 (16.743 sec)
INFO:tensorflow:probabilities = [[0.00000192 0.00063461 0.9981766  0.0002907  0.0000525  0.00000645
  0.00004817 0.00027612 0.00039549 0.00011752]
 [0.00000541 0.00000385 0.00005726 0.9980598  0.00000106 0.00068178
  0.00000016 0.00000861 0.00006612 0.00111596]
 [0.004176   0.0000016  0.00126337 0.00007631 0.00299826 0.00020909
  0.0000031  0.0340977  0.00136551 0.9558091 ]
 [0.00000085 0.00000224 0.00009645 0.9985543  0.00000001 0.00029126
  0.00000001 0.00000017 0.00074221 0.00031242]
 [0.0000133  0.00000555 0.00007891 0.00000076 0.00027495 0.00002457
  0.999584   0.00000015 0.000017   0.00000082]
 [0.99991834 0.00000001 0.00000165 0.00000053 0.00000001 0.00001306
  0.00001035 0.00000086 0.00005265 0.00000259]
 [0.00000166 0.00000158 0.00001118 0.00004765 0.00778502 0.00004649
  0.00000022 0.00045106 0.00015449 0.9915006 ]
 [0.001222   0.0004765  0.00096943 0.009587   0.00412907 0.001991
  0.00004557 0.07643187 0.00511999 0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.097998254.


## 評価(evaluate)

In [40]:
# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": eval_data},
    y=eval_labels,
    num_epochs=1,
    shuffle=False)
eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_results)

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-04-07-05:09:55
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-04-07-05:10:01
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9698, global_step = 20000, loss = 0.102002956
{'accuracy': 0.9698, 'loss': 0.102002956, 'global_step': 20000}
